In [ ]:
import matplotlib
%matplotlib inline
import numpy
import os

import datetime

# Import constants
# Create once the collection for this notebook
collection_id = None
import SEAScope.lib.utils
SEAScope.lib.utils.init_ids(20, 2000)

In [ ]:
# Class to disable printing
class HiddenPrints:
    def __enter__(self):
        self._original_stdout = sys.stdout
        sys.stdout = open(os.devnull, 'w')

    def __exit__(self, exc_type, exc_val, exc_tb):
        sys.stdout.close()
        sys.stdout = self._original_stdout
#SEAScope.upload.throttler.min_delay = 10
class empty_class():
    pass

**Read fronts already computed **

In [ ]:
import pickle
file = 'fronts_sst_bk.pyo'
with open(file, 'rb') as f:
    fronts = pickle.load(f)

In [ ]:
matplotlib.pyplot.figure(figsize=(20, 20))
print(fronts.keys())

#print(fronts['lon'])
for i in range(len(fronts['lon'])):
    if fronts['flag_front'][i] <= 2:
        matplotlib.pyplot.plot(fronts['lon'][i], fronts['lat'][i], 'k')
matplotlib.pyplot.savefig('test.png')

## Export wave rays to SEAScope

**Define Collection:** <br>
** A granule has to belong to a collection **<br>


In [ ]:
from SEAScope.lib.utils import create_collection, init_ids
# Make sure to keep the collection identifier, we will need it later
collection_id, collection = create_collection('User - Fronts detection')
print(collection_id)

# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155

import SEAScope.upload
with SEAScope.upload.connect(host, port) as link:
# Send create collection job
    SEAScope.upload.collection(link, collection)

**Upload granule to SEAScope: <br>
Define shell of granule, create granule <br>
The granule will contain each matrix of modified data as what we call a "field"<br>**
<span style="color:red">** Enter a name for each field (field_name_time) **</span></br>
**Upload collection and granule to SEAScope**

In [ ]:
from SEAScope.lib.utils import create_granule
# Shell of Granule
# Each position of the trajectory will be used as GCP
for c in range(len(fronts['lon'])):
    gcps = []
    for i in range(len(fronts['lon'][c])):
        if ~numpy.isnan(fronts['lon'][c][i]) :
            gcp = {'lon': fronts['lon'][c][i], 'lat': fronts['lat'][c][i], 'i': i, 'j': 0}
            gcps.append(gcp)

# Create granule
    #Start time of granule 
    dtstart = datetime.datetime.strptime(str(fronts["time_coverage_start"].decode()), "%Y%m%dT%H%M%SZ")
    dtstop = datetime.datetime.strptime(str(fronts["time_coverage_end"].decode()), "%Y%m%dT%H%M%SZ")
    #End time of granule 
    granule_id, granule = create_granule(collection_id, gcps, dtstart,dtstop)

# Set variables
# Enter a name for each variable field
    from SEAScope.lib.utils import set_field
    field_name_time ='fronts'
    set_field(granule, field_name_time, numpy.array(fronts['flags'][c]))

    # Send create granule job
    with SEAScope.upload.connect(host, port) as link:   
        SEAScope.upload.granule(link, granule)

**Telling SEAScope what to display: <br>
 The next step is variables definition. ** <br>
**<span style="color:red"> Enter a name for each variable you want to display (variable_name_time, ...) </span>**</br>

In [ ]:
from SEAScope.lib.utils import create_variable

# Create a variable for each parameter
variable_name_time = 'Front'
var1 = create_variable(collection, variable_name_time, [field_name_time], dims=1)

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)

** Telling SEAScope how to display variables: <br>
The rendering options are defined in the following cell. <br>
<span style="color:red"> You can play with min, max values, the colormap ... and check how the rendering changes on SEAScope </span>
**

In [ ]:
# Rendering configuration for the time
rcfg1 = var1['rendering']
rcfg1['min'] = 1
rcfg1['max'] = 6
rcfg1['colormap'] = 'jet'
rcfg1['zindex'] = .923
rcfg1['opacity'] = 0.8



# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)

<span style="color:green">** Go back to SEAScope and display the User Wave ray collection on top of the Globcurrent geostrophy **</span>